Zadanie 2. 

Wybierz jeden z plików csv z poprzednich ćwiczeń (Mini Kurs, Actors.csv, Names.csv ect..) lub inny plik z dbfs:/databricks-datasets/ i na jego podstawie stwórz schemat danych. Przykład na wykładzie.  

Użyj funckji spark.read. i stwórz DataFrame (DataFrameReader) wczytując plik z użyciem schematu, który stworzyłeś. 

In [0]:
display(dbutils.fs.ls("dbfs:/databricks-datasets/COVID/covid-19-data/"))


path name size modificationTime dbfs:/databricks-datasets/COVID/covid-19-data/.git/ .git/ 0 0 dbfs:/databricks-datasets/COVID/covid-19-data/.github/ .github/ 0 0 dbfs:/databricks-datasets/COVID/covid-19-data/.gitignore .gitignore 10 1615898767000 dbfs:/databricks-datasets/COVID/covid-19-data/LICENSE LICENSE 1289 1615898767000 dbfs:/databricks-datasets/COVID/covid-19-data/NEW-YORK-DEATHS-METHODOLOGY.md NEW-YORK-DEATHS-METHODOLOGY.md 2771 1615898767000 dbfs:/databricks-datasets/COVID/covid-19-data/NYT-readme.md NYT-readme.md 1748 1586273566000 dbfs:/databricks-datasets/COVID/covid-19-data/PROBABLE-CASES-NOTE.md PROBABLE-CASES-NOTE.md 3162 1615898767000 dbfs:/databricks-datasets/COVID/covid-19-data/README.md README.md 22959 1615898767000 dbfs:/databricks-datasets/COVID/covid-19-data/colleges/ colleges/ 0 0 dbfs:/databricks-datasets/COVID/covid-19-data/excess-deaths/ excess-deaths/ 0 0 dbfs:/databricks-datasets/COVID/covid-19-data/live/ live/ 0 0 dbfs:/databricks-datasets/COVID/covid-19-data/mask-use/ mask-use/ 0 0 dbfs:/databricks-datasets/COVID/covid-19-data/us-counties-recent.csv us-counties-recent.csv 3977154 1615898768000 dbfs:/databricks-datasets/COVID/covid-19-data/us-counties.csv us-counties.csv 45452100 1615898768000 dbfs:/databricks-datasets/COVID/covid-19-data/us-states.csv us-states.csv 703102 1615898768000 dbfs:/databricks-datasets/COVID/covid-19-data/us.csv us.csv 10269 1615898768000

In [0]:
#to see how does this look like
dbutils.fs.head("dbfs:/databricks-datasets/COVID/covid-19-data/us-counties.csv", 50)

In [0]:
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, DateType

schema = StructType([
    StructField("date", StringType(), True),
    StructField("county", StringType(), True),
    StructField("state", StringType(), True),
    StructField("fips", IntegerType(), True),
    StructField("cases", IntegerType(), True),
    StructField("deaths", IntegerType(), True)
])


path = "dbfs:/databricks-datasets/COVID/covid-19-data/us-counties.csv"

df = spark.read.format("csv").option("header", "true").option("delimiter", ",").option("quote", '"').schema(schema).load(path)


df.printSchema() 
df.show(10)

root
 |-- date: string (nullable = true)
 |-- county: string (nullable = true)
 |-- state: string (nullable = true)
 |-- fips: integer (nullable = true)
 |-- cases: integer (nullable = true)
 |-- deaths: integer (nullable = true)

+----------+-----------+----------+-----+-----+------+
|      date|     county|     state| fips|cases|deaths|
+----------+-----------+----------+-----+-----+------+
|2020-01-21|  Snohomish|Washington|53061|    1|     0|
|2020-01-22|  Snohomish|Washington|53061|    1|     0|
|2020-01-23|  Snohomish|Washington|53061|    1|     0|
|2020-01-24|       Cook|  Illinois|17031|    1|     0|
|2020-01-24|  Snohomish|Washington|53061|    1|     0|
|2020-01-25|     Orange|California| 6059|    1|     0|
|2020-01-25|       Cook|  Illinois|17031|    1|     0|
|2020-01-25|  Snohomish|Washington|53061|    1|     0|
|2020-01-26|   Maricopa|   Arizona| 4013|    1|     0|
|2020-01-26|Los Angeles|California| 6037|    1|     0|
+----------+-----------+----------+-----+-----+------+

Zadanie 3 

Użycie Read Modes.  

Wykorzystaj posiadane pliki bądź użyj nowe.  Użyj Sparka do odczytania jednego pliku i użyj wszystkich typów read modes. Poprawny plik nie wywoła żadnych efektów, więc popsuj dane tak aby każda z read modes zadziałał. 

In [0]:
from pyspark.sql.functions import when, col
df_corrupted = df.withColumn("fips",when(col("county") == "Snohomish", "flips").otherwise(col("fips"))).withColumn("deaths", when(col("state") == "Illinois", "NaN").otherwise(col("deaths")))

display(df_corrupted.limit(10))
df_corrupted.limit(10).write.format("csv").mode("overwrite").option("header", "true").save("dbfs:/FileStore/tables/us-counties-corrupted.csv")

filePath2 = "dbfs:/FileStore/tables/us-counties-corrupted.csv"

date county state fips cases deaths 2020-01-21 Snohomish Washington flips 1 0 2020-01-22 Snohomish Washington flips 1 0 2020-01-23 Snohomish Washington flips 1 0 2020-01-24 Cook Illinois 17031 1 NaN 2020-01-24 Snohomish Washington flips 1 0 2020-01-25 Orange California 6059 1 0 2020-01-25 Cook Illinois 17031 1 NaN 2020-01-25 Snohomish Washington flips 1 0 2020-01-26 Maricopa Arizona 4013 1 0 2020-01-26 Los Angeles California 6037 1 0

In [0]:
#PERMISSIVE - Inserts null for corrupted rows
df_permissive = spark.read.format("csv") \
    .option("header", "true") \
    .option("mode", "PERMISSIVE") \
    .schema(schema) \
    .load(filePath2)
display(df_permissive.limit(10))

#DROPMALFORMED - Skips malformed rows
df_dropmalformed = spark.read.format("csv") \
    .option("header", "true") \
    .option("mode", "DROPMALFORMED") \
    .schema(schema) \
    .load(filePath2)

display(df_dropmalformed.limit(10))

#FAILFAST - Stops reading at the first error
df_failfast = spark.read.format("csv") \
    .option("header", "true") \
    .option("mode", "FAILFAST") \
    .schema(schema) \
    .load(filePath2)

display(df_failfast.limit(10))

date county state fips cases deaths 2020-01-21 Snohomish Washington null 1 0 2020-01-22 Snohomish Washington null 1 0 2020-01-23 Snohomish Washington null 1 0 2020-01-24 Cook Illinois 17031 1 null 2020-01-24 Snohomish Washington null 1 0 2020-01-25 Orange California 6059 1 0 2020-01-25 Cook Illinois 17031 1 null 2020-01-25 Snohomish Washington null 1 0 2020-01-26 Maricopa Arizona 4013 1 0 2020-01-26 Los Angeles California 6037 1 0

date county state fips cases deaths 2020-01-25 Orange California 6059 1 0 2020-01-26 Maricopa Arizona 4013 1 0 2020-01-26 Los Angeles California 6037 1 0

org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 69.0 failed 1 times, most recent failure: Lost task 0.0 in stage 69.0 (TID 536) (ip-10-172-228-2.us-west-2.compute.internal executor driver): com.databricks.sql.io.FileReadException: Error while reading file dbfs:/FileStore/tables/us-counties-corrupted.csv/part-00000-tid-4439091527033067830-057e058a-7eb9-414f-b3ef-9f370bb4d12f-533-1-c000.csv.
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1$$anon$2.logFileNameAndThrow(FileScanRDD.scala:704)
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1$$anon$2.getNext(FileScanRDD.scala:673)
	at org.apache.spark.util.NextIterator.hasNext(NextIterator.scala:73)
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1.nextIterator(FileScanRDD.scala:796)
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1.$anonfun$hasNext$1(FileScanRDD.scala:496)
	at scala.runtime.java8.JFunction0$mcZ$sp.apply(JFunction0$mcZ$sp.java:23)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1.hasNext(FileScanRDD.scala:486)
	at scala.collection.Iterator$$anon$10.hasNext(Iterator.scala:460)
	at org.apache.spark.sql.execution.collect.UnsafeRowBatchUtils$.encodeUnsafeRows(UnsafeRowBatchUtils.scala:82)
	at org.apache.spark.sql.execution.collect.Collector.$anonfun$processFunc$1(Collector.scala:208)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$3(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$1(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.runTask(ResultTask.scala:55)
	at org.apache.spark.scheduler.Task.doRunTask(Task.scala:179)
	at org.apache.spark.scheduler.Task.$anonfun$run$5(Task.scala:142)
	at com.databricks.unity.EmptyHandle$.runWithAndClose(UCSHandle.scala:126)
	at org.apache.spark.scheduler.Task.$anonfun$run$1(Task.scala:142)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.Task.run(Task.scala:97)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$13(Executor.scala:904)
	at org.apache.spark.util.Utils$.tryWithSafeFinally(Utils.scala:1741)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$4(Executor.scala:907)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:23)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.executor.Executor$TaskRunner.run(Executor.scala:761)
	at java.util.concurrent.ThreadPoolExecutor.runWorker(ThreadPoolExecutor.java:1149)
	at java.util.concurrent.ThreadPoolExecutor$Worker.run(ThreadPoolExecutor.java:624)
	at java.lang.Thread.run(Thread.java:750)
Caused by: org.apache.spark.SparkException: Malformed records are detected in record parsing. Parse Mode: FAILFAST. To process malformed records as null result, try setting the option 'mode' as 'PERMISSIVE'.
	at org.apache.spark.sql.errors.QueryExecutionErrors$.malformedRecordsDetectedInRecordParsingError(QueryExecutionErrors.scala:1936)
	at org.apache.spark.sql.catalyst.util.FailureSafeParser.parse(FailureSafeParser.scala:103)
	at org.apache.spark.sql.catalyst.csv.UnivocityParser$.$anonfun$parseIterator$2(UnivocityParser.scala:507)
	at scala.collection.Iterator$$anon$11.nextCur(Iterator.scala:486)
	at scala.collection.Iterator$$anon$11.hasNext(Iterator.scala:492)
	at org.apache.spark.util.CompletionIterator.hasNext(CompletionIterator.scala:31)
	at scala.collection.Iterator$$anon$10.hasNext(Iterator.scala:460)
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1$$anon$2.getNext(FileScanRDD.scala:619)
	... 29 more
Caused by: org.apache.spark.sql.catalyst.util.BadRe

Zadanie 4 

Użycie DataFrameWriter. 

Zapisz jeden z wybranych plików do formatów (‘.parquet’, ‘.json’). Sprawdź, czy dane są zapisane poprawnie, użyj do tego spark.read (DataFrameReader).  

In [0]:

df_corrupted.write.format("parquet").mode("overwrite").save("dbfs:/FileStore/tables/us-counties-corrupted.parquet")
df_corrupted.write.format("json").mode("overwrite").save("dbfs:/FileStore/tables/us-counties-corrupted.json")

df_parquet = spark.read.format("parquet").load("dbfs:/FileStore/tables/us-counties-corrupted.parquet")
df_json = spark.read.format("json").load("dbfs:/FileStore/tables/us-counties-corrupted.json")

display(df_json)
display(df_parquet)


cases county date deaths fips state 1 Snohomish 2020-01-21 0 flips Washington 1 Snohomish 2020-01-22 0 flips Washington 1 Snohomish 2020-01-23 0 flips Washington 1 Cook 2020-01-24 NaN 17031 Illinois 1 Snohomish 2020-01-24 0 flips Washington 1 Orange 2020-01-25 0 6059 California 1 Cook 2020-01-25 NaN 17031 Illinois 1 Snohomish 2020-01-25 0 flips Washington 1 Maricopa 2020-01-26 0 4013 Arizona 1 Los Angeles 2020-01-26 0 6037 California 1 Orange 2020-01-26 0 6059 California 1 Cook 2020-01-26 NaN 17031 Illinois 1 Snohomish 2020-01-26 0 flips Washington 1 Maricopa 2020-01-27 0 4013 Arizona 1 Los Angeles 2020-01-27 0 6037 California 1 Orange 2020-01-27 0 6059 California 1 Cook 2020-01-27 NaN 17031 Illinois 1 Snohomish 2020-01-27 0 flips Washington 1 Maricopa 2020-01-28 0 4013 Arizona 1 Los Angeles 2020-01-28 0 6037 California 1 Orange 2020-01-28 0 6059 California 1 Cook 2020-01-28 NaN 17031 Illinois 1 Snohomish 2020-01-28 0 flips Washington 1 Maricopa 2020-01-29 0 4013 Arizona 1 Los Angeles 2020-01-29 0 6037 California 1 Orange 2020-01-29 0 6059 California 1 Cook 2020-01-29 NaN 17031 Illinois 1 Snohomish 2020-01-29 0 flips Washington 1 Maricopa 2020-01-30 0 4013 Arizona 1 Los Angeles 2020-01-30 0 6037 California 1 Orange 2020-01-30 0 6059 California 2 Cook 2020-01-30 NaN 17031 Illinois 1 Snohomish 2020-01-30 0 flips Washington 1 Maricopa 2020-01-31 0 4013 Arizona 1 Los Angeles 2020-01-31 0 6037 California 1 Orange 2020-01-31 0 6059 California 1 Santa Clara 2020-01-31 0 6085 California 2 Cook 2020-01-31 NaN 17031 Illinois 1 Snohomish 2020-01-31 0 flips Washington 1 Maricopa 2020-02-01 0 4013 Arizona 1 Los Angeles 2020-02-01 0 6037 California 1 Orange 2020-02-01 0 6059 California 1 Santa Clara 2020-02-01 0 6085 California 2 Cook 2020-02-01 NaN 17031 Illinois 1 Suffolk 2020-02-01 0 25025 Massachusetts 1 Snohomish 2020-02-01 0 flips Washington 1 Maricopa 2020-02-02 0 4013 Arizona 1 Los Angeles 2020-02-02 0 6037 California 1 Orange 2020-02-02 0 6059 California 2 San Francisco 2020-02-02 0 6075 California 2 Santa Clara 2020-02-02 0 6085 California 2 Cook 2020-02-02 NaN 17031 Illinois 1 Suffolk 2020-02-02 0 25025 Massachusetts 1 Snohomish 2020-02-02 0 flips Washington 1 Maricopa 2020-02-03 0 4013 Arizona 1 Los Angeles 2020-02-03 0 6037 California 1 Orange 2020-02-03 0 6059 California 2 San Francisco 2020-02-03 0 6075 California 2 Santa Clara 2020-02-03 0 6085 California 2 Cook 2020-02-03 NaN 17031 Illinois 1 Suffolk 2020-02-03 0 25025 Massachusetts 1 Snohomish 2020-02-03 0 flips Washington 1 Maricopa 2020-02-04 0 4013 Arizona 1 Los Angeles 2020-02-04 0 6037 California 1 Orange 2020-02-04 0 6059 California 2 San Francisco 2020-02-04 0 6075 California 2 Santa Clara 2020-02-04 0 6085 California 2 Cook 2020-02-04 NaN 17031 Illinois 1 Suffolk 2020-02-04 0 25025 Massachusetts 1 Snohomish 2020-02-04 0 flips Washington 1 Maricopa 2020-02-05 0 4013 Arizona 1 Los Angeles 2020-02-05 0 6037 California 1 Orange 2020-02-05 0 6059 California 2 San Francisco 2020-02-05 0 6075 California 2 Santa Clara 2020-02-05 0 6085 California 2 Cook 2020-02-05 NaN 17031 Illinois 1 Suffolk 2020-02-05 0 25025 Massachusetts 1 Snohomish 2020-02-05 0 flips Washington 1 Dane 2020-02-05 0 55025 Wisconsin 1 Maricopa 2020-02-06 0 4013 Arizona 1 Los Angeles 2020-02-06 0 6037 California 1 Orange 2020-02-06 0 6059 California 2 San Francisco 2020-02-06 0 6075 California 2 Santa Clara 2020-02-06 0 6085 California 2 Cook 2020-02-06 NaN 17031 Illinois 1 Suffolk 2020-02-06 0 25025 Massachusetts 1 Snohomish 2020-02-06 0 flips Washington 1 Dane 2020-02-06 0 55025 Wisconsin 1 Maricopa 2020-02-07 0 4013 Arizona 1 Los Angeles 2020-02-07 0 6037 California 1 Orange 2020-02-07 0 6059 California 2 San Francisco 2020-02-07 0 6075 California 2 Santa Clara 2020-02-07 0 6085 California 2 Cook 2020-02-07 NaN 17031 Illinois 1 Suffolk 2020-02-07 0 25025 Massachusetts 1 Snohomish 2020-02-07 0 flips Washington 1 Dane 2020-02-07 0 55025 Wisconsin 1 Maricopa 2020-02-08 0 4013 Arizona 1 Los Angeles 2020-02

date county state fips cases deaths 2020-10-10 Tucker West Virginia 54093 46 0 2020-10-10 Tyler West Virginia 54095 20 0 2020-10-10 Upshur West Virginia 54097 175 0 2020-10-10 Wayne West Virginia 54099 437 11 2020-10-10 Webster West Virginia 54101 9 0 2020-10-10 Wetzel West Virginia 54103 68 0 2020-10-10 Wirt West Virginia 54105 20 0 2020-10-10 Wood West Virginia 54107 408 6 2020-10-10 Wyoming West Virginia 54109 136 5 2020-10-10 Adams Wisconsin 55001 316 4 2020-10-10 Ashland Wisconsin 55003 197 2 2020-10-10 Barron Wisconsin 55005 624 6 2020-10-10 Bayfield Wisconsin 55007 156 1 2020-10-10 Brown Wisconsin 55009 11936 75 2020-10-10 Buffalo Wisconsin 55011 178 2 2020-10-10 Burnett Wisconsin 55013 256 4 2020-10-10 Calumet Wisconsin 55015 1868 7 2020-10-10 Chippewa Wisconsin 55017 814 0 2020-10-10 Clark Wisconsin 55019 579 9 2020-10-10 Columbia Wisconsin 55021 1113 3 2020-10-10 Crawford Wisconsin 55023 244 0 2020-10-10 Dane Wisconsin 55025 11722 44 2020-10-10 Dodge Wisconsin 55027 2546 19 2020-10-10 Door Wisconsin 55029 523 4 2020-10-10 Douglas Wisconsin 55031 622 0 2020-10-10 Dunn Wisconsin 55033 795 1 2020-10-10 Eau Claire Wisconsin 55035 2362 8 2020-10-10 Florence Wisconsin 55037 129 2 2020-10-10 Fond du Lac Wisconsin 55039 2877 15 2020-10-10 Forest Wisconsin 55041 366 7 2020-10-10 Grant Wisconsin 55043 1438 19 2020-10-10 Green Wisconsin 55045 683 3 2020-10-10 Green Lake Wisconsin 55047 508 1 2020-10-10 Iowa Wisconsin 55049 301 0 2020-10-10 Iron Wisconsin 55051 159 1 2020-10-10 Jackson Wisconsin 55053 209 1 2020-10-10 Jefferson Wisconsin 55055 1931 8 2020-10-10 Juneau Wisconsin 55057 520 2 2020-10-10 Kenosha Wisconsin 55059 4389 68 2020-10-10 Kewaunee Wisconsin 55061 807 3 2020-10-10 La Crosse Wisconsin 55063 3664 10 2020-10-10 Lafayette Wisconsin 55065 404 0 2020-10-10 Langlade Wisconsin 55067 422 2 2020-10-10 Lincoln Wisconsin 55069 417 3 2020-10-10 Manitowoc Wisconsin 55071 1845 5 2020-10-10 Marathon Wisconsin 55073 2577 30 2020-10-10 Marinette Wisconsin 55075 1311 9 2020-10-10 Marquette Wisconsin 55077 402 2 2020-10-10 Menominee Wisconsin 55078 158 0 2020-10-10 Milwaukee Wisconsin 55079 33953 549 2020-10-10 Monroe Wisconsin 55081 776 3 2020-10-10 Oconto Wisconsin 55083 1540 4 2020-10-10 Oneida Wisconsin 55085 730 5 2020-10-10 Outagamie Wisconsin 55087 6683 37 2020-10-10 Ozaukee Wisconsin 55089 1745 21 2020-10-10 Pepin Wisconsin 55091 80 0 2020-10-10 Pierce Wisconsin 55093 776 7 2020-10-10 Polk Wisconsin 55095 332 2 2020-10-10 Portage Wisconsin 55097 1877 14 2020-10-10 Price Wisconsin 55099 228 0 2020-10-10 Racine Wisconsin 55101 6092 99 2020-10-10 Richland Wisconsin 55103 300 4 2020-10-10 Rock Wisconsin 55105 3416 36 2020-10-10 Rusk Wisconsin 55107 99 1 2020-10-10 Sauk Wisconsin 55111 1249 6 2020-10-10 Sawyer Wisconsin 55113 279 1 2020-10-10 Shawano Wisconsin 55115 1522 7 2020-10-10 Sheboygan Wisconsin 55117 2711 20 2020-10-10 St. Croix Wisconsin 55109 1247 9 2020-10-10 Taylor Wisconsin 55119 280 4 2020-10-10 Trempealeau Wisconsin 55121 807 2 2020-10-10 Unknown Wisconsin null 0 10 2020-10-10 Vernon Wisconsin 55123 360 1 2020-10-10 Vilas Wisconsin 55125 352 1 2020-10-10 Walworth Wisconsin 55127 3094 36 2020-10-10 Washburn Wisconsin 55129 155 2 2020-10-10 Washington Wisconsin 55131 3340 37 2020-10-10 Waukesha Wisconsin 55133 9704 97 2020-10-10 Waupaca Wisconsin 55135 1697 24 2020-10-10 Waushara Wisconsin 55137 583 3 2020-10-10 Winnebago Wisconsin 55139 6228 41 2020-10-10 Wood Wisconsin 55141 1149 7 2020-10-10 Albany Wyoming 56001 826 0 2020-10-10 Big Horn Wyoming 56003 105 2 2020-10-10 Campbell Wyoming 56005 453 2 2020-10-10 Carbon Wyoming 56007 255 2 2020-10-10 Converse Wyoming 56009 188 0 2020-10-10 Crook Wyoming 56011 63 0 2020-10-10 Fremont Wyoming 56013 898 14 2020-10-10 Goshen Wyoming 56015 127 2 2020-10-10 Hot Springs Wyoming 56017 42 0 2020-10-10 Johnson Wyoming 56019 47 1 2020-10-10 Laramie Wyoming 56021 918 4 2020-10-10 Lincoln Wyoming 56023 262 1 2020-10-10 Natrona Wyoming 56025 754 7 2020-10-10 Niobrara Wyoming 560